In [1]:
import pandas as pd

In [2]:

df_crop_details = pd.read_excel('./data/2.xlsx', sheet_name=1)

In [3]:
# 去除空格
df_crop_details['cropName'] = df_crop_details['cropName'].apply(lambda x: x.strip())
# CropType = [x.strip() for x in CropType]


In [4]:
df_crop_planting = pd.read_excel('./data/2.xlsx', sheet_name=0)
# 照例去除一下空格
df_crop_planting['cropName'] = df_crop_planting['cropName'].apply(lambda x: x.strip())
# ffill
df_crop_planting['landName'] = df_crop_planting['landName'].ffill()
df_crop_planting

landName  cropNum cropName cropType  plantArea season
0        A1        6       小麦       粮食       80.0     单季
1        A2        7       玉米       粮食       55.0     单季
2        A3        7       玉米       粮食       35.0     单季
3        A4        1       黄豆   粮食（豆类）       72.0     单季
4        A5        4       绿豆   粮食（豆类）       68.0     单季
..      ...      ...      ...      ...        ...    ...
82       F3       28      小青菜      蔬菜         0.3    第二季
83       F3       30       生菜      蔬菜         0.3    第二季
84       F4       19       芸豆   蔬菜（豆类）        0.6    第一季
85       F4       34       芹菜      蔬菜         0.3    第二季
86       F4       23       菠菜      蔬菜         0.3    第二季

[87 rows x 6 columns]

In [5]:

unit_profit_lsc = []
for line in df_crop_details.values:
    s = str(line[7]).split('-')
    unit_profit_lsc.append((float(s[0]) + float(s[1])) / 2 * line[5] - line[6])
df_crop_details['unitProfit'] = unit_profit_lsc
df_crop_details

no  cropNum cropName cropLandType season  unitYield  cost       price  \
0      1        1       黄豆          平旱地     单季        400   400   2.50-4.00   
1      2        2       黑豆          平旱地     单季        500   400   6.50-8.50   
2      3        3       红豆          平旱地     单季        400   350   7.50-9.00   
3      4        4       绿豆          平旱地     单季        350   350   6.00-8.00   
4      5        5       爬豆          平旱地     单季        415   350   6.00-7.50   
..   ...      ...      ...          ...    ...        ...   ...         ...   
120  103       30       生菜         智慧大棚    第二季       4500  2200   5.40-7.20   
121  104       31       辣椒         智慧大棚    第二季       1800  1300  7.20-10.20   
122  105       32      空心菜         智慧大棚    第二季      11000  5500   3.60-7.20   
123  106       33      黄心菜         智慧大棚    第二季       5400  2750   4.80-6.00   
124  107       34       芹菜         智慧大棚    第二季       6000  1200   3.80-5.80   

     unitProfit  
0        900.00  
1       3350.00  
2       2950.00  
3       2100.00  
4       2451.25  
..          ...  
120    26150.00  
121    14360.00  
122    53900.00  
123    26410.00  
124    27600.00  

[125 rows x 9 columns]

In [6]:
# 搞一下季节和年份的集合
SeasonType = ["单季", "第一季", "第二季"]
SeasonDict = {"单季": 1, "第一季": 1, "第二季": 2}
SeasonNum = [1, 2]
years = [2024, 2025, 2026, 2027, 2028, 2029, 2030]

In [7]:
# 枚举地块类型
LandType = {"A": "平旱地", "B": "梯田", "C": "山坡地", "D": "水浇地", "E": "普通大棚", "F": "智慧大棚"}
# LandType

In [8]:
# 枚举地块
LandName = df_crop_planting['landName'].unique()
# LandName

In [9]:
# 读入作物名称
CropName = df_crop_details['cropName'].unique()
# CropName

In [10]:
any([x[-1] == ' ' for x in CropName])
# 居然有空格
# 现在去掉了

False

In [11]:
# 亩产量
unit_yield_lsc = {
    l: {
        s: {
            c: df_crop_details[
                (df_crop_details['cropName'] == c) &
                (df_crop_details['cropLandType'] == l) &
                (df_crop_details['season'] == s)
                ]['unitYield'].values[0] if df_crop_details[
                                                (df_crop_details['cropName'] == c) &
                                                (df_crop_details['cropLandType'] == l) &
                                                (df_crop_details['season'] == s)
                                                ]['unitYield'].values.size > 0 else 0
            for c in CropName
        } for s in SeasonType
    }
    for l in LandType.values()
}

# unit_yield

In [12]:
# 亩利润
unit_profit_lsc = {
    l: {
        s: {
            c: df_crop_details[
                (df_crop_details['cropName'] == c) &
                (df_crop_details['cropLandType'] == l) &
                (df_crop_details['season'] == s)
                ]['unitProfit'].values[0]
            if df_crop_details[
                   (df_crop_details['cropName'] == c) &
                   (df_crop_details['cropLandType'] == l) &
                   (df_crop_details['season'] == s)
                   ]['unitYield'].values.size > 0 else 0
            for c in CropName
        } for s in SeasonType
    }
    for l in LandType.values()
}

# unit_profit

In [13]:
# 每种作物的总需求
crop_demand = {
    c: 0
    for c in CropName
}

# 这里需要另一张表
# 代码独立出来移到上面去了

for line in df_crop_planting.values:
    # 面积*该土地类型的亩产量    面积                      地块类型字典 地块类型     季节     作物名称
    crop_demand[line[2]] += line[4] * unit_yield_lsc[LandType[line[0][0]]][line[5]][line[2]]

# crop_demand

In [14]:
# 准备开搞
from pulp import LpMaximize, LpProblem, LpVariable, lpSum, value, LpInteger, PULP_CBC_CMD, LpContinuous, LpBinary


In [15]:
model = LpProblem("Crop_Planting_Optimization_with_Specific_Rules", LpMaximize)

In [16]:
# %timeit X = LpVariable.dicts("X", (CropName, LandName, years, seasons), lowBound=0, cat=LpContinuous)
# %timeit XX = LpVariable.dicts("X", [(c, l, y, s) for c in CropName for l in LandName for y in years for s in seasons],lowBound=0, cat=LpContinuous)

In [17]:
# 地块l在y年的s季的种植c的量
# X = LpVariable.dicts("crop_plant_area", (CropName, LandName, years, SeasonType), lowBound=0, cat=LpContinuous)
X = LpVariable.dicts("X", [(c, l, y, s)
                           for c in CropName
                           for l in LandName
                           for y in years
                           for s in SeasonType],
                     lowBound=0,
                     cat=LpContinuous
                     )
# X

In [18]:
# 地块l在y年的s季是否种植了c
# Y = LpVariable.dicts("crop_plant_bool", (CropName, LandName, years, SeasonType), cat=LpBinary)
Y = LpVariable.dicts("Y", [(c, l, y, s) for c in CropName for l in LandName for y in years for s in SeasonType],
                     cat=LpBinary)

# Y

In [19]:
# 确保与X进行01约束
for c in CropName:
    for l in LandName:
        for y in years:
            for s in SeasonType:
                # 如果种植了作物，则种植面积大于0
                model += X[c, l, y, s] <= 10000000 * Y[c, l, y, s], f"PlantingConstraint1_{c}_{l}_{y}_{s}"
                # 如果未种植作物，则种植面积为0
                model += X[c, l, y, s] >= 0.000001 * Y[c, l, y, s], f"PlantingConstraint2_{c}_{l}_{y}_{s}"

In [21]:
# 目标函数：总利润 = sum(x[i]*profit[c,l,s])
model += lpSum(
    X[c,l,y,s] * unit_profit_lsc[LandType[l[0]]][s][c]
    for c in CropName
    for l in LandName
    for y in years
    for s in SeasonType
)


In [ ]:
# 每个季节每种作物的种植量必须小于需求量
for c in CropName:
    